# TripAdvisor Crawler and Parser
The Python notebook enables one to scrape hotels from TripAdvisor.com, leveraging the power of LXML, DOM and Python requests library. Further, this work happens to include prilimnary ETL work on the extracted hotel fields. This work shall be a predecessor to another ipynb notebook detailing the Data Cleaning and ETL process in full swing.

# Part I: Download and Collect Hotel URLs.
Download Main Webpage and collect the Hotel URLs recursivley from webpages there on..

In [3]:
# import libraries
import os
import requests
import json
import re
import sys
import lxml.html 
from lxml import html
from lxml import etree
import csv
import pandas as pd
import numpy as np
from geopy.geocoders import Nominatim

print('All required libraries have been successfully imported.')

All required libraries have been successfully imported.


In [4]:
def download_only_page(url, filename):
    """""
    Input: 
    -----
        url- URL of the webpage to be downloaded to local file system.
        filename- Desired filename to be associated with the downloaded webpage.
    
    Output:
    ------
        return nothing.
    
    Functionality:
    -------------
        Request for the webpage based on URL and download it to a local directory.
    """""
    # Request to download the html page
    r = requests.get(url)
    
    # Save downloaded page as a text file
    with open(filename, mode='wb') as file:     
        file.write(r.content)

    print('TripAdvisor- hotel HTML page downloaded successfully..')   

In [5]:
def download_html_page(url, count_file):
    """""
    Input: 
    -----
        url- URL of the webpage to be downloaded to local file system.
        count_file- file number or file count, used to create a filename to be stored in local directory.
    
    Output:
    ------
        return lxml.etree instance(html) and the updated count aka file number.
    
    Functionality:
    -------------
        - Request for the webpage based on URL and download it to a local directory.
        - Create lxml.etree instance of the webpage downloaded, inorder to help parse it.
    """""
     # Request to download the html page
    r = requests.get(url)
    count_file += 1
    # Save downloaded page as a text file
    filename = 'Project-Dataset/tripadvisor_canada_hotels'+ str(count_file) + '.txt'
    with open(filename, mode='wb') as file:     
        file.write(r.content)

    print('TripAdvisor- hotel HTML page downloaded successfully..')
    
    # Open saved file to parse it.
    with open(filename,'r') as fileread:
        html = etree.HTML(fileread.read())
    
    # Parse the HTML page as a tree structure
    result = etree.tostring(html, pretty_print=True, method="html")
    print('File read successfully..')
    
    return html, count_file

In [8]:
def read_parse_file(filename):
    """""
    Input: 
    -----
        filename- Filename used to store the desired webpage in local directory.
    
    Output:
    ------
        return lxml.etree instance(html) and the updated count/file number.
    
    Functionality:
    -------------
        - Read the desired file from local directory.
        - Create lxml.etree instance of the webpage downloaded inorder to help parse it.
    """""
    # Open saved file to parse it.
    with open(filename,'r') as fileread:
        html = etree.HTML(fileread.read())
    
    # Parse the HTML page as a tree structure
    result = etree.tostring(html, pretty_print=True, method="html")
    print('File read successfully..')
    
    return html

In [7]:
def get_hotel_url(count, html):
    """""
    Input: 
    -----
        count- Number of desired elements(here the 'divs' containing hotel URLs) present in the downloaded page.
        html- lxml.etree instance(html), used to parse the file.
    
    Output:
    ------
        return the extracted full hotel URL(hotel_url) from the base webpage.
    
    Functionality:
    -------------
        - Parse the downloaded file using html.etree and XPATH to obtain hotel URLs embedded in the mainpage.
        - This function considers only exact search results for a given category of hotels.
    """""
    hotel_url = []
    double_count = 0
    num_ad = 2 # to counter ads intbetween
    iter_val = 0
    
    # Parse html page to get the urls for nested webpages.
    for element in range(int(count)):
        iter_val = element + 1
        # Adjust numbering based on webpage structure.
        if iter_val <= 4 :
            iter_val = iter_val
        elif iter_val == int(count):
            iter_val += int(double_count * num_ad) 
        else:
            if (iter_val % 5 == 0) & (iter_val != int(count)):
                double_count += 1
                iter_val += int(double_count * num_ad)
            else:
                iter_val += int(double_count * num_ad)
                
        # Use xpath to retrieve the necessary content.
        XPATH = html.xpath('//*[@id="taplc_hsx_hotel_list_lite_dusty_hotels_combined_sponsored_0"]/div/div[' + str(iter_val) + ']/div/div[1]/@data-url')

        if str(XPATH)[2:-2] == '':
            XPATH = html.xpath('//*[@id="taplc_hsx_hotel_list_lite_dusty_hotels_combined_sponsored_0"]/div[' + str(iter_val) + ']/div/div[1]/@data-url')
        
        if str(XPATH)[2:-2] == '':
            XPATH = html.xpath('//*[@id="taplc_hsx_hotel_list_lite_dusty_hotels_combined_sponsored_0"]/div/div[' + str(iter_val) + ']/div/div/div/div[1]/@data-url')
        
        hotel_url.append('https://www.tripadvisor.ca' + str(XPATH)[2:-2])
    
    return hotel_url

In [8]:
def get_hotel_url_related(count, html):
    """""
    Input: 
    -----
        count- Number of desired elements(here the 'divs' containing hotel URLs) present in the downloaded page.
        html- lxml.etree instance(html), used to parse the file.
    
    Output:
    ------
        return the extracted full hotel URL(hotel_url) from the base webpage.
    
    Functionality:
    -------------
        - Parse the downloaded file using html.etree and XPATH to obtain hotel URLs embedded in the mainpage.
        - This function considers only related search results (if exact results are nil, this will be called)
          for a given category of hotels.
    """""
    hotel_url = []
    double_count = 0
    num_ad = 2 # to counter ads intbetween
    iter_val = 0
    
    # Parse html page to get the urls for nested webpages.
    for element in range(int(count)):
        iter_val = element + 1
        # Adjust numbering based on webpage structure.
        if iter_val <= 4 :
            iter_val = iter_val
        elif iter_val == int(count):
            iter_val += int(double_count * num_ad) 
        else:
            if (iter_val % 5 == 0) & (iter_val != int(count)):
                double_count += 1
                iter_val += int(double_count * num_ad)
            else:
                iter_val += int(double_count * num_ad)
        value = iter_val + 1
    
        # Use xpath to retrieve the necessary content.
        XPATH = html.xpath('//*[@id="taplc_hsx_hotel_list_lite_dusty_filtered_out_hotels_0"]/div/div[' + str(value) + ']/div/div[1]/@data-url')
        
        if str(XPATH)[2:-2] == '':
            XPATH = html.xpath('//*[@id="taplc_hsx_hotel_list_lite_dusty_filtered_out_hotels_0"]/div[' + str(value) + ']/div/div[1]/@data-url')

        hotel_url.append('https://www.tripadvisor.ca' + str(XPATH)[2:-2])
    
    return hotel_url

In [9]:
def get_hotel_url_nomatches(count, html):
    """""
    Input: 
    -----
        count- Number of desired elements(here the 'divs' containing hotel URLs) present in the downloaded page.
        html- lxml.etree instance(html), used to parse the file.
    
    Output:
    ------
        return the extracted full hotel URL(hotel_url) from the base webpage.
    
    Functionality:
    -------------
        - Parse the downloaded file using html.etree and XPATH to obtain hotel URLs embedded in the mainpage.
        - This function considers only other search results (if exact results and related results for a page are nil, 
          this will be called) for a given category of hotels.
    """""
    hotel_url = []
    double_count = 0
    num_ad = 2 # to counter ads intbetween
    iter_val = 0
    
    # Parse html page to get the urls for nested webpages.
    for element in range(int(count)):
        iter_val = element + 1
        # Adjust numbering based on webpage structure.
        if iter_val <= 4 :
            iter_val = iter_val
        elif iter_val == int(count):
            iter_val += int(double_count * num_ad) 
        else:
            if (iter_val % 5 == 0) & (iter_val != int(count)):
                double_count += 1
                iter_val += int(double_count * num_ad)
            else:
                iter_val += int(double_count * num_ad)
    
        # Use xpath to retrieve the necessary content.
        XPATH = html.xpath('//*[@id="taplc_hsx_hotel_list_lite_dusty_ab_hotels_sponsored_0"]/div[' + str(iter_val) + ']/div/div[1]/@data-url')
        
        if str(XPATH)[2:-2] == '':
            XPATH =  html.xpath('//*[@id="taplc_hsx_hotel_list_lite_dusty_ab_hotels_sponsored_0"]/div[' + str(iter_val) + ']/div/div/div/div[1]/@data-url')

        hotel_url.append('https://www.tripadvisor.ca' + str(XPATH)[2:-2])
    
    return hotel_url

In [8]:
# Extract related content from the tree using XPath for the MainPage of TripAdvisor hotels canada.
count_file = 0

# Request html page
url = str('https://www.tripadvisor.ca/Hotels-g153339-Canada-Hotels.html')
html, count_file = download_html_page(url, count_file)

# Create xpath to access necessary content
XPATH_MAINPAGE = '//*[@id="taplc_hsx_hotel_list_lite_dusty_hotels_combined_sponsored_0"]//div[@class="prw_rup prw_meta_hsx_responsive_listing ui_section listItem"]'
hotel_main_page = html.xpath(XPATH_MAINPAGE)

# Get count of elements of interest in html page
count = html.xpath('count(//*[@id="taplc_hsx_hotel_list_lite_dusty_hotels_combined_sponsored_0"]//div[@class="prw_rup prw_meta_hsx_responsive_listing ui_section listItem"])')
# print(count)

# Get the parsed html etree
hotel_url_returned = get_hotel_url(count, html)
print('Content Extracted..')

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
Content Extracted..


In [9]:
# Convert list to dataframe
hotel_url_df = pd.DataFrame(np.array(hotel_url_returned))
print(hotel_url_df[:30])
print('30 Hotel URLs retrieved..')

#  Write to csv file
hotel_url_df.to_csv('Project-Dataset/final-data/file_mainpage_url.txt', index=False)
print('Written on to file..')

                                                    0
0   https://www.tripadvisor.ca/Hotel_Review-g15499...
1   https://www.tripadvisor.ca/Hotel_Review-g15501...
2   https://www.tripadvisor.ca/Hotel_Review-g15494...
3   https://www.tripadvisor.ca/Hotel_Review-g15503...
4   https://www.tripadvisor.ca/Hotel_Review-g15491...
5   https://www.tripadvisor.ca/Hotel_Review-g15499...
6   https://www.tripadvisor.ca/Hotel_Review-g15494...
7   https://www.tripadvisor.ca/Hotel_Review-g15501...
8   https://www.tripadvisor.ca/Hotel_Review-g15503...
9   https://www.tripadvisor.ca/Hotel_Review-g15491...
10  https://www.tripadvisor.ca/Hotel_Review-g15502...
11  https://www.tripadvisor.ca/Hotel_Review-g15499...
12  https://www.tripadvisor.ca/Hotel_Review-g15494...
13  https://www.tripadvisor.ca/Hotel_Review-g15501...
14  https://www.tripadvisor.ca/Hotel_Review-g10226...
15  https://www.tripadvisor.ca/Hotel_Review-g15503...
16  https://www.tripadvisor.ca/Hotel_Review-g15494...
17  https://www.tripadvisor.

In [10]:
# Count number of pages needs to parsed further.
num_pages = int(str(html.xpath('//*[@id="taplc_hotels_leaf_geo_list_dusty_hotels_resp_0"]/div/div[21]/div/div/@data-numpages'))[2:-2])
base_pages_toscrape = num_pages
print('number of pages to scrape', num_pages)

number of pages to scrape 52


In [11]:
# Get the content of mainpage so as to make recursivepages-call for all other subsequent pages from it.
hotel_pages = []
value = 0
cut = 0

# Get count of elements of interest in html page
count_pages = html.xpath('//*[@id="taplc_main_pagination_bar_dusty_hotels_resp_0"]/div/div/div/span[2]/@onclick')
split_string = str(count_pages).split(',')
# print(split_string)
    
hotel_page = split_string[-1]
hotel_page = hotel_page[2:-5]
group = hotel_page.split('-')

In [12]:
# Create urls of inner webpages to make recursive calls
for iter_val in range(num_pages-1):
    hotel_page = ''
    for iter_val in range(len(group)):
        if iter_val == 2:
            value += 20
            group[2] = 'oa' + str(value)
        hotel_page += str(group[iter_val]) + str('-')
        if value >= 1080:
                cut = 1
                break
    if cut == 1:
        break
    hotel_page = hotel_page[:-1]
    #print(hotel_page)
    
    # Make url for embedded html pages.
    url = str('https://www.tripadvisor.ca') + str(hotel_page) + str('#LEAF_GEO_LIST')
    hotel_pages.append(str(url))
    # Get count of elements of interest in html page
    count = html.xpath('count(//*[@id="taplc_hsx_hotel_list_lite_dusty_hotels_combined_sponsored_0"]//div[@class="prw_rup prw_meta_hsx_responsive_listing ui_section listItem"])')

    # Get the etree instance for parsing html page of interest.
    html, count_file = download_html_page(url, count_file)
    
    # Get the embedded urls in the current html page being parsed.
    hotel_url_returned = get_hotel_url(int(count), html)
    print('url: '+ str(url))
    #print(count)

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
url: https://www.tripadvisor.ca/Hotels-g153339-oa20-Canada-Hotels.html#LEAF_GEO_LIST
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
url: https://www.tripadvisor.ca/Hotels-g153339-oa40-Canada-Hotels.html#LEAF_GEO_LIST
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
url: https://www.tripadvisor.ca/Hotels-g153339-oa60-Canada-Hotels.html#LEAF_GEO_LIST
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
url: https://www.tripadvisor.ca/Hotels-g153339-oa80-Canada-Hotels.html#LEAF_GEO_LIST
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
url: https://www.tripadvisor.ca/Hotels-g153339-oa100-Canada-Hotels.html#LEAF_GEO_LIST
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
url: https://www.tripadvisor.ca/Hotels-g153339-oa120-Canada-Hotels.html#LEAF_GEO_LIST
TripAdvi

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
url: https://www.tripadvisor.ca/Hotels-g153339-oa1020-Canada-Hotels.html#LEAF_GEO_LIST


In [13]:
# Write to csv file
hotels_url_df_new = pd.DataFrame(np.array(hotel_pages))
hotels_url_df_new.to_csv('Project-Dataset/file_HotelPage_url.txt', index=False)
print('Written on to file..')

Written on to file..


In [14]:
# Recursively Hit 2-52 pages downloaded to get the hotel urls.
pages_url = []

for iter_val in range(num_pages-2):
    page_number = iter_val + 2
    filename = 'Project-Dataset/tripadvisor_canada_hotels'+ str(page_number) + '.txt'
    print('filename:', filename)
    html = read_parse_file(filename)
    count = html.xpath('count(//*[@id="taplc_broad_geo_tiles_dusty_hotels_resp_0"]/ul/li)')
    print(count)
    for i in range(int(count)):
        i += 1
        call_pages_link = html.xpath('//*[@id="taplc_broad_geo_tiles_dusty_hotels_resp_0"]/ul/li[' + str(i) + ']/a/@href')
        pages_url.append(str(str('https://www.tripadvisor.ca') + str(call_pages_link)[2:-2]))   

filename: Project-Dataset/tripadvisor_canada_hotels2.txt
File read successfully..
20.0
filename: Project-Dataset/tripadvisor_canada_hotels3.txt
File read successfully..
20.0
filename: Project-Dataset/tripadvisor_canada_hotels4.txt
File read successfully..
20.0
filename: Project-Dataset/tripadvisor_canada_hotels5.txt
File read successfully..
20.0
filename: Project-Dataset/tripadvisor_canada_hotels6.txt
File read successfully..
20.0
filename: Project-Dataset/tripadvisor_canada_hotels7.txt
File read successfully..
20.0
filename: Project-Dataset/tripadvisor_canada_hotels8.txt
File read successfully..
20.0
filename: Project-Dataset/tripadvisor_canada_hotels9.txt
File read successfully..
20.0
filename: Project-Dataset/tripadvisor_canada_hotels10.txt
File read successfully..
20.0
filename: Project-Dataset/tripadvisor_canada_hotels11.txt
File read successfully..
20.0
filename: Project-Dataset/tripadvisor_canada_hotels12.txt
File read successfully..
20.0
filename: Project-Dataset/tripadvisor_ca

In [15]:
# Write to csv file
pages_url_df_new = pd.DataFrame(np.array(pages_url))
pages_url_df_new.to_csv('Project-Dataset/file_innerpages_url.txt', index=False)
print('Written on to file..')

Written on to file..


In [16]:
print(len(pages_url_df_new))
pages_url_df_new.head(5)

1000


0
0  https://www.tripadvisor.ca/Hotels-g154918-Jasp...
1  https://www.tripadvisor.ca/Hotels-g181727-Canm...
2  https://www.tripadvisor.ca/Hotels-g155023-Char...
3  https://www.tripadvisor.ca/Hotels-g4041681-Kit...
4  https://www.tripadvisor.ca/Hotels-g154937-Pent...

In [17]:
length = len(pages_url_df_new)
print(length)

1000


In [18]:
# Download hotel html pages.
for iter_val in range(length):
    url = pages_url[iter_val]
    print(count_file)
    html,count_file = download_html_page(url, count_file)

52
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
53
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
54
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
55
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
56
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
57
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
58
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
59
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
60
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
61
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
62
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
63
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
64
T

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
152
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
153
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
154
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
155
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
156
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
157
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
158
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
159
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
160
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
161
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
162
TripAdvisor- hotel HTML page downloaded successfully..
File read successfull

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
250
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
251
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
252
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
253
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
254
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
255
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
256
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
257
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
258
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
259
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
260
TripAdvisor- hotel HTML page downloaded successfully..
File read successfull

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
348
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
349
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
350
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
351
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
352
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
353
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
354
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
355
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
356
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
357
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
358
TripAdvisor- hotel HTML page downloaded successfully..
File read successfull

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
446
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
447
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
448
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
449
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
450
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
451
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
452
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
453
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
454
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
455
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
456
TripAdvisor- hotel HTML page downloaded successfully..
File read successfull

...

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
642
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
643
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
644
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
645
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
646
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
647
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
648
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
649
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
650
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
651
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
652
TripAdvisor- hotel HTML page downloaded successfully..
File read successfull

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
740
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
741
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
742
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
743
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
744
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
745
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
746
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
747
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
748
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
749
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
750
TripAdvisor- hotel HTML page downloaded successfully..
File read successfull

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
838
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
839
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
840
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
841
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
842
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
843
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
844
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
845
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
846
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
847
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
848
TripAdvisor- hotel HTML page downloaded successfully..
File read successfull

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
936
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
937
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
938
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
939
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
940
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
941
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
942
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
943
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
944
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
945
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
946
TripAdvisor- hotel HTML page downloaded successfully..
File read successfull

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1034
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1035
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1036
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1037
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1038
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1039
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1040
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1041
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1042
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1043
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1044
TripAdvisor- hotel HTML page downloaded successfully..
File read 

In [19]:
# Initialize values
start_val = base_pages_toscrape + 1
hotel_urls = []
file_num = 1052
sum_urls = 30
max_urls_perpage = 30
cut = 0

# Hit pages to download all the embedded urls
for iter_val in range(length):
    value = 0
    count_file = start_val + iter_val
    # Create filename to parse the html page.
    filename = 'Project-Dataset/tripadvisor_canada_hotels'+ str(count_file) + '.txt'
    # print('filename:', filename)

    # Parse the html page and get etree instance.
    html = read_parse_file(filename)
    
    # Get count of elements of interest in the html page.
    count = html.xpath('count(//*[@id="taplc_hsx_hotel_list_lite_dusty_hotels_combined_sponsored_0"]//div[@class="prw_rup prw_meta_hsx_responsive_listing ui_section listItem"])')
    if count > max_urls_perpage:
        count = max_urls_perpage
    print('count:',count)
    
    # Get number of pages to recursively hit to get hotel URLs.
    num_pages = str(html.xpath('//*[@id="taplc_main_pagination_bar_dusty_hotels_resp_0"]/div/div/div/@data-numpages'))[2:-2]
    if num_pages == '':
        num_pages = 1
    num_pages = int(num_pages)
    
    # Load urls from the list of mainpage URLS we had created previously.
    url = pages_url[iter_val]
    # print('url:',url,"\n")
    
    # Create xpath to get the URL links.
    path = html.xpath('//*[@id="taplc_main_pagination_bar_dusty_hotels_resp_0"]/div/div/div/a/@href')
    split_string = str(path).split(',')
    hotel_page = split_string[-1]
    hotel_page = hotel_page[2:-5]
    group = hotel_page.split('-')
    # print('path',path,"\n")
        
    for i in range(num_pages):
        i += 1
        cut = 0
        hotel_page = ''
        if i == 1:
            url = url
        else:
            for iter_val in range(len(group)):
                if iter_val == 2:
                    value += 30
                    group[2] = 'oa' + str(value)
                hotel_page += str(group[iter_val]) + str('-')
            hotel_page = hotel_page[:-1]
            # print(hotel_page)
     
            # Create URLs for the inner URLs obtained.
            url = str('https://www.tripadvisor.ca') + str(hotel_page)
            hotel_pages.append(str(url))
            
            # Download the inner pages.
            html, file_num = download_html_page(url, file_num)
            
            # Count the number of elements of interest in the html page.
            count = html.xpath('count(//*[@id="taplc_hsx_hotel_list_lite_dusty_hotels_combined_sponsored_0"]//div[@class="prw_rup prw_meta_hsx_responsive_listing ui_section listItem"])')
            print('count:',count)
        
        # If count returns 0 previously try an alternate xpath.
        if count == 0.0:
            count = html.xpath('count(//*[@id="taplc_hsx_hotel_list_lite_dusty_filtered_out_hotels_0"]//div[@class="prw_rup prw_meta_hsx_responsive_listing ui_section listItem"])')
            print('count-related:',count)
            cut = 1
             # If count returns 0 previously try an alternate xpath.
            if count == 0.0:
                count = html.xpath('count(//*[@id="taplc_hsx_hotel_list_lite_dusty_ab_hotels_sponsored_0"]//div[@class="prw_rup prw_meta_hsx_responsive_listing ui_section listItem"])')
                print('count-nomtaches:',count)
                cut = 2
        print('url: '+ str(url) + "\n")
         
        # Call the respective parse functions written for the xpath type element obtained.
        if cut == 0:
            temp = get_hotel_url(int(count), html)
        elif cut == 1:
            temp = get_hotel_url_related(int(count), html)
        elif cut == 2:
            temp = get_hotel_url_nomatches(int(count), html)
        url_list = str(temp)[1:-1]
        url_list = url_list.split(',')
        length_url_list = len(url_list)
         
        # Clean retrieved data to form proper tripadvisor structured URLS and add to list.
        for j in range(length_url_list):
            urls = str(url_list[j])
            
            if ((j == 0) & (str(urls)[1:-1]).startswith('https://www.tripadvisor.ca/Hotel')):
                urls = urls[0:]
                hotel_urls.append(str(urls)[1:-1])
                print('inner urls:',str(urls)[1:-1])
                sum_urls += 1
            elif str(urls)[2:-1] != 'https://www.tripadvisor.ca':
                if j == length_url_list:
                    urls = urls[:-1]
                    
                if (str(urls)[2:-1]).startswith('https://www.tripadvisor.ca/Hotel') | (str(urls)[1:-1]).startswith('https://www.tripadvisor.ca/Hotel'):
                    hotel_urls.append(str(urls)[2:-1])
                    print('inner urls:',str(urls)[2:-1])
                    sum_urls += 1

count_file = file_num

print('\nNumber of Hotels URLs retrieved in total ', sum_urls)
print('\nNumber of Hotels URLs retrieved in this pass', len(hotel_urls))

File read successfully..
count: 30.0
url: https://www.tripadvisor.ca/Hotels-g154918-Jasper_Jasper_National_Park_Alberta-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d182314-Reviews-Mount_Robson_Inn-Jasper_Jasper_National_Park_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d182307-Reviews-Crimson_Jasper-Jasper_Jasper_National_Park_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d252985-Reviews-Bear_Hill_Lodge-Jasper_Jasper_National_Park_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d184493-Reviews-Chateau_Jasper-Jasper_Jasper_National_Park_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d184491-Reviews-Maligne_Lodge-Jasper_Jasper_National_Park_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d182313-Reviews-Marmot_Lodge-Jasper_Jasper_National_Park_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d182314-Reviews

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
count: 0.0
count-related: 17.0
url: https://www.tripadvisor.ca/Hotels-g154918-oa90-Jasper_Jasper_National_Park_Alberta-Hotels.html#BODY

inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d672464-Reviews-All_Seasons_Accommodations-Jasper_Jasper_National_Park_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d622094-Reviews-804_Miette_Guest_House-Jasper_Jasper_National_Park_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d2209363-Reviews-Doe_a_Deer_Accommodation-Jasper_Jasper_National_Park_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d1580256-Reviews-Blue_Moose_Inn-Jasper_Jasper_National_Park_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d2210737-Reviews-Cabin_Creek_Jasper-Jasper_Jasper_National_Park_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g154918-d12987460-Reviews-Cedargat

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
count: 0.0
count-related: 29.0
url: https://www.tripadvisor.ca/Hotels-g181727-oa60-Canmore_Kananaskis_Country_Alberta-Hotels.html#BODY

inner urls: https://www.tripadvisor.ca/Hotel_Review-g181727-d1022284-Reviews-Riverview_Main-Canmore_Kananaskis_Country_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g181727-d6913646-Reviews-Bow_River_Campground-Canmore_Kananaskis_Country_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g181727-d3674361-Reviews-The_Canmore_Hotel-Canmore_Kananaskis_Country_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g181727-d12669005-Reviews-Room_with_a_view_Bed_and_Breakfast-Canmore_Kananaskis_Country_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g181727-d3254435-Reviews-Burnside_House-Canmore_Kananaskis_Country_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g181727-d504347-Reviews-Quilters_Inn_Bed_a

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
count: 28.0
url: https://www.tripadvisor.ca/Hotels-g155023-oa30-Charlottetown_Prince_Edward_Island-Hotels.html#BODY

inner urls: https://www.tripadvisor.ca/Hotel_Review-g155023-d544004-Reviews-Charlotte_s_Rose_Inn-Charlottetown_Prince_Edward_Island.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g155023-d664131-Reviews-Charlottetown_Backpackers_Inn-Charlottetown_Prince_Edward_Island.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g155023-d1494133-Reviews-Glendenning_Hall-Charlottetown_Prince_Edward_Island.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g155023-d1817091-Reviews-Northside_B_B-Charlottetown_Prince_Edward_Island.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g155023-d8113335-Reviews-The_Eden_Hall_Inn-Charlottetown_Prince_Edward_Island.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g155023-d3300234-Reviews-A_Country_Home_Bed_Breakfast-Charlottetown_

url: https://www.tripadvisor.ca/Hotels-g4041681-Kitimat_Stikine_District_British_Columbia-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g181770-d182075-Reviews-Best_Western_Terrace_Inn-Terrace_Kitimat_Stikine_District_British_Columbia.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g181770-d242103-Reviews-Days_Inn_by_Wyndham_Terrace-Terrace_Kitimat_Stikine_District_British_Columbia.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g671271-d8460769-Reviews-Microtel_Inn_Suites_by_Wyndham_Kitimat-Kitimat_Kitimat_Stikine_District_British_Columb.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g3350815-d7818274-Reviews-Red_Goat_Lodge-Iskut_Kitimat_Stikine_District_British_Columbia.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g671271-d12301526-Reviews-Mstar_Hotel-Kitimat_Kitimat_Stikine_District_British_Columbia.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g10521894-d10006340-Reviews-Holiday_Inn_Express_Suites_Terrace-Thornhi

...

count: 2.0
url: https://www.tripadvisor.ca/Hotels-g1746273-Oyen_Alberta-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g1746273-d1628738-Reviews-Canalta_Oyen-Oyen_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g1746273-d7645675-Reviews-Antelope_Inn_Motel-Oyen_Alberta.html
File read successfully..
count: 2.0
url: https://www.tripadvisor.ca/Hotels-g2426287-Consort_Alberta-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g2426287-d6947760-Reviews-Prairie_Moon_Inn_Suites-Consort_Alberta.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g2426287-d2416773-Reviews-Sunrise_Motel-Consort_Alberta.html
File read successfully..
count: 1.0
url: https://www.tripadvisor.ca/Hotels-g155031-Matagami_Quebec-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g155031-d3440922-Reviews-Hotel_Matagami-Matagami_Quebec.html
File read successfully..
count: 1.0
url: https://www.tripadvisor.ca/Hotels-g1131916-Schefferville_Quebec-Hotels.html


TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
count: 0.0
count-related: 1.0
url: https://www.tripadvisor.ca/Hotels-g1125988-oa30-Killarney_Northeastern_Ontario_Ontario-Hotels.html#BODY

inner urls: https://www.tripadvisor.ca/Hotel_Review-g1125988-d557706-Reviews-Killarney_Mountain_Lodge-Killarney_Northeastern_Ontario_Ontario.html
File read successfully..
count: 0.0
count-related: 2.0
url: https://www.tripadvisor.ca/Hotels-g499327-Wellington_Prince_Edward_Island-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g499327-d8462614-Reviews-Chez_Yvette_Bed_Breakfast-Wellington_Prince_Edward_Island.html
inner urls: https://www.tripadvisor.ca/Hotel_Review-g499327-d273287-Reviews-Le_Village_de_l_Acadie-Wellington_Prince_Edward_Island.html
File read successfully..
count: 1.0
url: https://www.tripadvisor.ca/Hotels-g499375-Sainte_Catherine_de_la_Jacques_Cartier_Quebec-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g499375-d596694-R

File read successfully..
count: 0.0
count-related: 1.0
url: https://www.tripadvisor.ca/Hotels-g3199084-Pennfield_Ridge_New_Brunswick-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g3199084-d3333192-Reviews-Smith_s_Motel_Ltd-Pennfield_Ridge_New_Brunswick.html
File read successfully..
count: 0.0
count-related: 1.0
url: https://www.tripadvisor.ca/Hotels-g7092272-Minton_Saskatchewan-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g7092272-d7085459-Reviews-Minton_Hotel-Minton_Saskatchewan.html
File read successfully..
count: 1.0
url: https://www.tripadvisor.ca/Hotels-g3199052-Ile_de_la_Grande_Entree_Iles_de_la_Madeleine_Quebec-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g3199052-d1673480-Reviews-Auberge_la_Salicorne-Ile_de_la_Grande_Entree_Iles_de_la_Madeleine_Quebec.html
File read successfully..
count: 0.0
count-related: 1.0
url: https://www.tripadvisor.ca/Hotels-g4702405-Nimmo_Islet_British_Columbia-Hotels.html

inner urls: https://w

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
count: 0.0
count-related: 1.0
url: https://www.tripadvisor.ca/Hotels-g3738264-oa30-Hamiota_Manitoba-Hotels.html#BODY

File read successfully..
count: 0.0
count-related: 0.0
count-nomtaches: 30.0
url: https://www.tripadvisor.ca/Hotels-g950953-Riverview_Albert_County_New_Brunswick-Hotels.html

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
count: 0.0
count-related: 1.0
url: https://www.tripadvisor.ca/Hotels-g950953-oa30-Riverview_Albert_County_New_Brunswick-Hotels.html#BODY

File read successfully..
count: 1.0
url: https://www.tripadvisor.ca/Hotels-g13279845-Saint_Anthony_Prince_Edward_Island-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g13279845-d183484-Reviews-Mill_River_Resort-Saint_Anthony_Prince_Edward_Island.html
File read successfully..
count: 0.0
count-related: 0.0
count-nomtaches: 30.0
url: https://www.tripadvisor.ca/Hotels-g15721000-Eastgate_Briti

File read successfully..
count: 1.0
url: https://www.tripadvisor.ca/Hotels-g1924377-L_Ile_Perrot_Quebec-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g1924377-d2621318-Reviews-Motel_Montreal-L_Ile_Perrot_Quebec.html
File read successfully..
count: 0.0
count-related: 1.0
url: https://www.tripadvisor.ca/Hotels-g2137386-Charlevoix_Quebec-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g2137386-d1099765-Reviews-Cap_Sur_Mer_House-Charlevoix_Quebec.html
File read successfully..
count: 1.0
url: https://www.tripadvisor.ca/Hotels-g660787-Liscomb_Mills_Nova_Scotia-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g660787-d262654-Reviews-Liscombe_Lodge_Resort_and_Conference_Center-Liscomb_Mills_Nova_Scotia.html
File read successfully..
count: 1.0
url: https://www.tripadvisor.ca/Hotels-g1113387-Englehart_Northeastern_Ontario_Ontario-Hotels.html

inner urls: https://www.tripadvisor.ca/Hotel_Review-g1113387-d4341075-Reviews-Englehart_Motel-Englehart

In [22]:
# Convert the URL list to pandas dataframe.
urls_df = pd.DataFrame(np.array(hotel_urls))
urls_df.head()

#  Write to csv file- append the current retrieved URLs with the 30 URLs got already.
with open('Project-Dataset/final-data/file_mainpage_url.txt', 'a') as fd:
    urls_df.to_csv(fd, index=False, header=False)

In [26]:
# Recursively Hit 2-52 page links downloaded to get the hotel urls.
review_ratings = []
hotel_full_urllist = pd.read_csv("Project-Dataset/final-data/file_mainpage_url.txt")
print(len(hotel_full_urllist))
print('Hotel urls CSV file read successfully..')

8996
Hotel urls CSV file read successfully..


In [27]:
hotel_full_urllist.head(10)

0
0  https://www.tripadvisor.ca/Hotel_Review-g15499...
1  https://www.tripadvisor.ca/Hotel_Review-g15501...
2  https://www.tripadvisor.ca/Hotel_Review-g15494...
3  https://www.tripadvisor.ca/Hotel_Review-g15503...
4  https://www.tripadvisor.ca/Hotel_Review-g15491...
5  https://www.tripadvisor.ca/Hotel_Review-g15499...
6  https://www.tripadvisor.ca/Hotel_Review-g15494...
7  https://www.tripadvisor.ca/Hotel_Review-g15501...
8  https://www.tripadvisor.ca/Hotel_Review-g15503...
9  https://www.tripadvisor.ca/Hotel_Review-g15491...

# Part II: Parse the downloaded hotel webpages to extract useful fields from them.
- Parse the hotel webpages sequentially to extract important fields such as user ratings, average rating, hotel name, location, etc,.
- Do basic ETL and cleaning for Null values such as dropping null values that cannot be retrieved through hits, aggregating values for fields for which a value can be obtained though it has null value post hits.
- De-duplicate the final dataframe obatined (both hotel information and reviews dataframe).

In [28]:
def get_overall_rating(html, XPATH_HOTELOVERALL_RATING, XPATH_OVERALLRATING_WORDS):
    """""
    Input: 
    -----
        html- lxml.etree instance(html), used to parse the file.
        XPATH_HOTELOVERALL_RATING- XPATH to be used to extract overall hotel rating.
        XPATH_OVERALLRATING_WORDS- XPATH to be used to extract overall hotel rating in words.
    
    Output:
    ------
        return extracted overall rating(overall_rating) and overallrating(hotel_rating_overall_word)
        in words fields.
    
    Functionality:
    -------------
        - Parse the downloaded file using html.etree and XPATH to obtain overall rating.
    """""
    overall_rating = str(html.xpath(XPATH_HOTELOVERALL_RATING))[2:-2]
    if overall_rating == '':
        overall_rating = str(html.xpath(XPATH_ALT_HOTELOVERALL_RATING))[2:-2]
    hotel_rating_overall_word = str(html.xpath(XPATH_OVERALLRATING_WORDS))[2:-2]
    
    return overall_rating, hotel_rating_overall_word

In [29]:
def get_address(html, XPATH_STADDRESS, XPATH_LOCALITY, XPATH_COUNTRY):
    """""
    Input: 
    -----
        html- lxml.etree instance(html), used to parse the file.
        XPATH_STADDRESS- XPATH to be used to extract street address of the hotel.
        XPATH_LOCALITY- XPATH to be used to extract locality of the hotel.
        XPATH_COUNTRY- XPATH to be used to extract country(location) information.
    
    Output:
    ------
        return street_name, locality_name, country_name, address_full, locality- corresponds
        to extracted streent name, cleaned locality name to obatin lat-lon, country, complete 
        address and original locality name respectively.
    
    Functionality:
    -------------
        - Parse the downloaded file using html.etree and XPATH to obtain address of the hotel.
    """""
    street = str(html.xpath(XPATH_STADDRESS)).split(',')
    street_name = str(street[0])[2:-1]
    locality = str(html.xpath(XPATH_LOCALITY)).split(',')
    
    if len(locality) > 6:
        try:
            locality_name = str(locality[2])[1:-8]
        except:
            locality_name = str(locality[2])[1:-1]
    else:
        try:
            locality_name = str(locality[0]+locality[1])[2:-8]
        except:
            locality_name = str(locality[0])[2:-1]
        
    country = str(html.xpath(XPATH_COUNTRY)).split(',')
    country_name = str(country[0])[2:-1]
    address_full = str(street_name + ' ' + locality_name)
    
    return street_name, locality_name, country_name, address_full, locality

In [30]:
def get_lat_long(address_full, locality):
    """""
    Input: 
    -----
        address_full- Complete address of the hotel, obtained after cleaning.
        locality- Locality of the hotel, obatined after cleaning.
    
    Output:
    ------
        return lat, lon- corresponds to the latitude and longitude of the hotel location.
    
    Functionality:
    -------------
        - Parse the downloaded file using html.etree and XPATH to obtain latitude, longitude
          information of the hotel.
        - If full address throws null, try to obatin just the locality's lat-lon.
        - If locality also throws null, try to obatin lat-lon of the province. 
        
    """""
    try:
        geolocator = Nominatim(user_agent="ITRS")
        location = geolocator.geocode(address_full)
        lat = location.latitude
        lon = location.longitude
        print((lat, lon))
    except:
        try:
            if len(locality) > 6:
                location = geolocator.geocode(str(locality[2])[1:-8])
            else:
                location = geolocator.geocode(str(locality[1])[1:-8])
            lat = location.latitude
            lon = location.longitude
            print((lat, lon))
        except:
            lat = 'nil'
            lon = 'nil'
            print("An exception occurred", (lat, lon))
    
    return lat, lon

In [31]:
def get_price(html, XPATH_PRICE):
    """""
    Input: 
    -----
        html- lxml.etree instance(html), used to parse the file.
        XPATH_PRICE- XPATH to be used to extract price for the hotel.
    
    Output:
    ------
        return price- price for the hotel. Consider the striked price(maximum) if available,
        else consider the best quoted price of all.
    
    Functionality:
    -------------
        - Parse the downloaded file using html.etree and XPATH to obtain price of the hotel.
    """""
    price = str(html.xpath(XPATH_PRICE))[4:-2]
    
    return price

In [32]:
def get_reviews(html, XPATH_REVIEW_NUMBER, XPATH_ALTREVIEW_NUMBER):
    """""
    Input: 
    -----
        html- lxml.etree instance(html), used to parse the file.
        XPATH_REVIEW_NUMBER- XPATH to obtain the total reviews present for the hotel.
        XPATH_ALTREVIEW_NUMBER- Alternate XPATH to obtain the total reviews present for the 
                                hotel.
    
    Output:
    ------
        return reviews- total number of reviews available for the hotel.
    
    Functionality:
    -------------
        - Parse the downloaded file using html.etree and XPATH to obtain total number of
          reviews present for the hotel.
    """""
    # Get total number of user reviews given for the hotel.
    reviews = str(html.xpath(XPATH_REVIEW_NUMBER))[2:-2]
    if reviews == '':
        reviews = str(html.xpath(XPATH_ALTREVIEW_NUMBER))[2:-2]
    reviews = re.findall("[0-9]", reviews)
    reviews = ''.join(reviews)
    
    # If total reviews is nil handle it.
    if reviews == '':
        reviews = 0 # need to handle condition to extract reviews
        user_rating = 'nil' 
        user_profile = 'nil' 
        user_name = 'nil' 
        review_date = 'nil'
        stay_date = 'nil'
        review_title = 'nil'
        review = 'nil'
    elif int(reviews) > 200:
        reviews = 200
    print(reviews)
        
    return reviews

In [21]:
# NOTE: This script will only download the first 5K hotel pages to local directory.
# Split urls to be hit into batches of 5k each.
length_df = int(len(hotel_full_urllist)/2)
print(length_df)
file_no = 0
batch = 'first'

# Run batch 1, from 1-4498
for iter_val in range(length_df):
    url = str(hotel_full_urllist.values[iter_val])[2:-2]
    #print(url)

    # Download the webpage
    file_no += 1
    filename = 'Project-Dataset/final-data/hotel_webpage'+ str(file_no) + '.txt'
    download_only_page(url, filename)
    
print('Batch 1- webpages download completed successfully')
file_num_value = file_no

4498
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripA

TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdviso

TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdviso

TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdviso

TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdviso

...

TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdviso

TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdviso

TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdviso

TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdviso

TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdvisor- hotel HTML page downloaded successfully..
TripAdviso

In [47]:
# NOTE: This script will only download the next/second 5K hotel pages to local directory.
# Run batch 2, from 4499-rest
batch = 'second'
file_no = length_df

for iter_val in range(length_df):
    file_count = length_df + iter_val
    url = str(hotel_full_urllist.values[file_count])[2:-2]
    #print(url)
    
    # Download the webpage
    file_no += 1
    filename = 'Project-Dataset/final-data/hotel_webpage'+ str(file_no) + '.txt'
    download_only_page(url, filename)
    
print('Batch 2- webpages download completed successfully')

Batch 2- webpages download completed successfully


### Master Script:
The following python piece of code (a script) helps to obtain all the fields mentioned above by recursively hitting inner URLs for obtaining user reviews,other user related information, hotel name, location and other hotel related information.

In [61]:
# This script will recursively hit hotel URLs and obtain all the information required from it.
# Initialize variables.
if batch == 'second':
    file_no = file_num_value - 1
    file_number = review_file_count
    hotel_count = hotel_left_count
else:
    file_no = 0
    file_number = 0
    hotel_count = 1

count = 3
loop_count = length_df/2
hotel_name = []
hotel_overall_rating = []
hotel_overall_rating_words = []
total_reviews = []
user_ratings = []
hotel_id = []
review_id = []
user_name = []
user_profile = []
user_review = []
user_reviewdate = []
user_staydate = []
hotel_price = []
address = []
lat_lon = []
amenities = []

# XPath for different hotel field to be retrieved.
XPATH_HOTELNAME = '//*[@id="HEADING"]/text()'
XPATH_ALT_HOTELOVERALL_RATING = '//*[@class="rating"]/span/text()'
XPATH_HOTELOVERALL_RATING = '//*[@class="hotels-hotel-review-about-with-photos-Reviews__overallRating--vElGA"]/text()'
XPATH_OVERALLRATING_WORDS = '//*[@class="hotels-hotel-review-about-with-photos-Reviews__ratingLabel--24XY2"]/text()'
XPATH_REVIEW_NUMBER = '//*[@class="hotels-hotel-review-about-with-photos-Reviews__seeAllReviews--3PpLR"]/text()'
XPATH_ALTREVIEW_NUMBER = '//*[@class="reviewCount "]/text()'
XPATH_ADDRESS = '//*[@class="public-business-listing-ContactInfo__nonWebLink--2rxPP"]/span/text()'
XPATH_STADDRESS = '//*[@class="street-address"]/text()'
XPATH_LOCALITY = '//*[@class="locality"]/text()'
XPATH_COUNTRY = '//*[@class="country-name"]/text()'
XPATH_PRICE = '//*[contains(@id, "bor_book_link_")]//div[contains(@class, "bb_price_text")]/text()'
XPATH_AMENITIES = '//*[@class="hotels-hotel-review-about-with-photos-Amenity__name--2IUMR"]/text()'

# Main body of the script where everything goes- extraction of information.
for iter_val in range(loop_count): 
    file_count = file_no + iter_val
    file_no += 1
    url = str(hotel_full_urllist.values[file_count])[2:-2]
    print(url)
    
    filename = 'Project-Dataset/final-data/hotel_webpage'+ str(file_no) + '.txt'
    download_only_page(url, filename)
    html = read_parse_file(filename)
    hotel_id.append(hotel_count)
    
    # Get hotel name
    name = str(html.xpath(XPATH_HOTELNAME))[2:-2]
    hotel_name.append(name)
    print(name)
    
    # Get overall hotel rating in figures and words.
    overall_rating, hotel_rating_overall_word = get_overall_rating(html, XPATH_HOTELOVERALL_RATING, XPATH_OVERALLRATING_WORDS)
    hotel_overall_rating.append(overall_rating.strip())
    hotel_overall_rating_words.append(hotel_rating_overall_word.strip())
    
    # Get address of hotels
    street_name, locality_name, country, address_full, locality = get_address(html, XPATH_STADDRESS, XPATH_LOCALITY, XPATH_COUNTRY)
    address.append(address_full)
    print(address_full)
    
    # Get (Latitude,Longitude) values for hotels
    lat, lon = get_lat_long(address_full, locality)
    lat_lon.append((lat, lon))
    
    # Get amenities
    amenities.append(html.xpath(XPATH_AMENITIES))
    
    # Get price
    price = get_price(html, XPATH_PRICE)
    hotel_price.append(price)
        
    # Get reviews- user profile, user ratings, date/time
    reviews_total =  get_reviews(html, XPATH_REVIEW_NUMBER, XPATH_ALTREVIEW_NUMBER)
    total_reviews.append(reviews_total)
    
    # Calculate the number of pages to parse based on total reviews present.
    if int(reviews_total) > 5:
        num_pages_reviews = int(int(reviews_total)/5)
        num_reviews_perpage = 5
    elif int(reviews_total) <= 5:
        num_pages_reviews = 1
        num_reviews_perpage = int(reviews_total)
    
    for iter_var_outer in range(int(num_pages_reviews)):
        count = 3
        val = 0
        
        # Create URLs to call next-next pages recursively
        url_reviews = url.split('-')
        if (iter_var_outer-1) >= 0:
            val = int(5 + ((iter_var_outer - 1) * 5))
            var = url_reviews[3]
            url_reviews[3] = str(var+'-or'+str(val)) 
            url_review = '-'.join(url_reviews)
            print(url_review)
            
            # Download html page and save it as a text file
            file_number += 1
            filename = 'Project-Dataset/final-data/hotel_reviews_webpage'+ str(file_number) + '.txt'
            download_only_page(url_review, filename)
            
            # Get etree instance to parse its content.
            html = read_parse_file(filename)
    
        for iter_var in range(num_reviews_perpage):
            review_count = iter_val + 1
            if review_count % 5 == 0:
                count = 3
                
            user_rating = str(html.xpath('//*[@id="component_24"]/div[3]/div/div[' + str(count) + ']//span[contains(@class, "ui_bubble_rating")]/@class'))[26:-2]
            if user_rating != '':
                user_rating = int(user_rating)/10
                print(user_rating)
            else:
                user_rating = 'nil'
                
            user_profiles = str(html.xpath('//*[@id="component_24"]/div[3]/div/div[' + str(count) + ']//a[@class="ui_header_link social-member-MemberEventOnObjectBlock__member--23Flv"]/@href'))[2:-2]
            if user_profiles != '':
                user_profiles = 'https://www.tripadvisor.ca' + user_profiles
            else:
                user_profiles = 'nil'
                
            user_names = str(html.xpath('//*[@id="component_24"]/div[3]/div/div[' + str(count) + ']//a[@class="ui_header_link social-member-MemberEventOnObjectBlock__member--23Flv"]/text()'))[2:-2]
            
            review_date = str(html.xpath('//*[@id="component_24"]/div[3]/div/div[' + str(count) + ']//div[@class="social-member-MemberEventOnObjectBlock__event_type--1lSEx"]/span/text()'))[18:-2]
            if review_date.lower() == 'yesterday':
                review_date = 'Mar. 22'
            if review_date == '':
                review_date = 'nil'
                
            
            stay_date = str(html.xpath('//*[@id="component_24"]/div[3]/div/div[' + str(count) + ']//div[@class="hotels-review-list-parts-EventDate__event_date--CRXs4"]/span/text()'))[2:-2]
            if stay_date == '':
                stay_date = 'nil'
            
            review_title = str(html.xpath('//*[@id="component_24"]/div[3]/div/div[' + str(count) + ']//a[@class="hotels-hotel-review-community-content-review-list-parts-ReviewTitle__reviewTitleText--2VUye"]/span/span/text()'))[2:-2]
            if review_title == '':
                review_title = ''
                
            review = str(html.xpath('//*[@id="component_24"]/div[3]/div/div[' + str(count) + ']//q[@class="hotels-hotel-review-community-content-review-list-parts-ExpandableReview__reviewText--2OVqJ"]/span//text()'))[2:-2]
            if review == '':
                review = 'nil'
            
            review_id.append(hotel_count)    
            user_ratings.append(user_rating)
            user_name.append(user_names)
            user_profile.append(user_profiles)
            user_review.append(str(review_title + " " + review))
            user_reviewdate.append(review_date)
            user_staydate.append(stay_date)
            count += 1
    hotel_count += 1
            
review_file_count = file_number
review_left_count = review_count
hotel_left_count = hotel_count
print("Batch- Collection successfully done..\n")

https://www.tripadvisor.ca/Hotel_Review-g793524-d9585424-Reviews-Willowood_RV_Resort_Campground-Amherstburg_Ontario.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
Willowood RV Resort & Campground
4610 Essex County Rd 1 Amherstburg Ontario
(50.000678, -86.000977)
16
https://www.tripadvisor.ca/Hotel_Review-g793524-d9585424-Reviews-or5-Willowood_RV_Resort_Campground-Amherstburg_Ontario.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1.0
3.0
3.0
5.0
5.0
https://www.tripadvisor.ca/Hotel_Review-g793524-d9585424-Reviews-or10-Willowood_RV_Resort_Campground-Amherstburg_Ontario.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
https://www.tripadvisor.ca/Hotel_Review-g984011-d7392367-Reviews-Canalta_Selkirk-Selkirk_Manitoba.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
Canalta Selkirk
1061 Manitoba Ave Selkirk Manitoba
(50.1493654, -96.8824933)
66
4.

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
5.0
5.0
5.0
5.0
5.0
https://www.tripadvisor.ca/Hotel_Review-g635950-d651396-Reviews-or25-Hearthstone_Inn_Port_Hawkesbury-Port_Hawkesbury_Cape_Breton_Island_Nova_Scotia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
3.0
3.0
3.0
3.0
3.0
https://www.tripadvisor.ca/Hotel_Review-g635950-d651396-Reviews-or30-Hearthstone_Inn_Port_Hawkesbury-Port_Hawkesbury_Cape_Breton_Island_Nova_Scotia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
4.0
4.0
4.0
4.0
4.0
https://www.tripadvisor.ca/Hotel_Review-g635950-d651396-Reviews-or35-Hearthstone_Inn_Port_Hawkesbury-Port_Hawkesbury_Cape_Breton_Island_Nova_Scotia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
https://www.tripadvisor.ca/Hotel_Review-g635950-d651396-Reviews-or40-Hearthstone_Inn_Port_Hawkesbury-Port_Hawkesbury_Cape_Breton_Island_Nova_Scotia.html
TripAdvi

https://www.tripadvisor.ca/Hotel_Review-g635950-d1097202-Reviews-or60-Mackenzie_House_Tourist_Home-Port_Hawkesbury_Cape_Breton_Island_Nova_Scotia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
5.0
3.0
4.0
5.0
5.0
https://www.tripadvisor.ca/Hotel_Review-g635950-d1097202-Reviews-or65-Mackenzie_House_Tourist_Home-Port_Hawkesbury_Cape_Breton_Island_Nova_Scotia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
4.0
3.0
1.0
https://www.tripadvisor.ca/Hotel_Review-g1488013-d1488191-Reviews-Camping_Chalets_Juneau-St_Augustin_de_Desmaures_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
Camping Chalets Juneau
155 Chemin du Lac St Augustin de Desmaures Quebec
(46.7494382, -71.4001394)
76
4.0
4.0
4.0
3.0
4.0
https://www.tripadvisor.ca/Hotel_Review-g1488013-d1488191-Reviews-or5-Camping_Chalets_Juneau-St_Augustin_de_Desmaures_Quebec.html
TripAdvisor- hotel HTML page downloaded successf

5.0
https://www.tripadvisor.ca/Hotel_Review-g681182-d649285-Reviews-or80-Moulin_Wakefield_Mill_Hotel_Spa-Wakefield_Outaouais_Region_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
5.0
5.0
5.0
5.0
5.0
https://www.tripadvisor.ca/Hotel_Review-g681182-d649285-Reviews-or85-Moulin_Wakefield_Mill_Hotel_Spa-Wakefield_Outaouais_Region_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
https://www.tripadvisor.ca/Hotel_Review-g681182-d649285-Reviews-or90-Moulin_Wakefield_Mill_Hotel_Spa-Wakefield_Outaouais_Region_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
https://www.tripadvisor.ca/Hotel_Review-g681182-d649285-Reviews-or95-Moulin_Wakefield_Mill_Hotel_Spa-Wakefield_Outaouais_Region_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
4.0
4.0
4.0
4.0
4.0
https://www.tripadvisor.ca/Hotel_Review-g681182-d649285-Reviews-or100-Moulin

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
5.0
5.0
5.0
5.0
5.0
https://www.tripadvisor.ca/Hotel_Review-g681182-d1756534-Reviews-or60-Les_Trois_Erables-Wakefield_Outaouais_Region_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
https://www.tripadvisor.ca/Hotel_Review-g681182-d1756534-Reviews-or65-Les_Trois_Erables-Wakefield_Outaouais_Region_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
5.0
5.0
5.0
5.0
5.0
https://www.tripadvisor.ca/Hotel_Review-g681182-d1756534-Reviews-or70-Les_Trois_Erables-Wakefield_Outaouais_Region_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
https://www.tripadvisor.ca/Hotel_Review-g681182-d1756534-Reviews-or75-Les_Trois_Erables-Wakefield_Outaouais_Region_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
https://www.tripadvisor.ca/Hotel_Review-g681182-d175

...

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
https://www.tripadvisor.ca/Hotel_Review-g181777-d182085-Reviews-or20-Poco_Inn_Suites_Hotel-Port_Coquitlam_British_Columbia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
https://www.tripadvisor.ca/Hotel_Review-g181777-d182085-Reviews-or25-Poco_Inn_Suites_Hotel-Port_Coquitlam_British_Columbia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
1.0
2.0
5.0
4.0
5.0
https://www.tripadvisor.ca/Hotel_Review-g181777-d182085-Reviews-or30-Poco_Inn_Suites_Hotel-Port_Coquitlam_British_Columbia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
4.0
5.0
3.0
3.0
5.0
https://www.tripadvisor.ca/Hotel_Review-g181777-d182085-Reviews-or35-Poco_Inn_Suites_Hotel-Port_Coquitlam_British_Columbia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
5.0
5.0
2.0
5.0
4.0
https://www.tripadvisor.ca/H

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
Oak Island Resort & Conference Centre
36 Treasure Drive Western Shore Nova Scotia
(44.5208079764344, -64.3083505372523)
200
5.0
5.0
5.0
3.0
5.0
https://www.tripadvisor.ca/Hotel_Review-g499241-d262655-Reviews-or5-Oak_Island_Resort_Conference_Centre-Western_Shore_Southwest_Nova_Scotia_Nova_Scotia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
5.0
2.0
5.0
1.0
3.0
https://www.tripadvisor.ca/Hotel_Review-g499241-d262655-Reviews-or10-Oak_Island_Resort_Conference_Centre-Western_Shore_Southwest_Nova_Scotia_Nova_Scotia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
2.0
5.0
4.0
3.0
4.0
https://www.tripadvisor.ca/Hotel_Review-g499241-d262655-Reviews-or15-Oak_Island_Resort_Conference_Centre-Western_Shore_Southwest_Nova_Scotia_Nova_Scotia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
https://www.tripadvisor

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
4.0
4.0
5.0
3.0
2.0
https://www.tripadvisor.ca/Hotel_Review-g499241-d262655-Reviews-or165-Oak_Island_Resort_Conference_Centre-Western_Shore_Southwest_Nova_Scotia_Nova_Scotia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
4.0
5.0
2.0
4.0
5.0
https://www.tripadvisor.ca/Hotel_Review-g499241-d262655-Reviews-or170-Oak_Island_Resort_Conference_Centre-Western_Shore_Southwest_Nova_Scotia_Nova_Scotia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
4.0
1.0
3.0
4.0
4.0
https://www.tripadvisor.ca/Hotel_Review-g499241-d262655-Reviews-or175-Oak_Island_Resort_Conference_Centre-Western_Shore_Southwest_Nova_Scotia_Nova_Scotia.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
https://www.tripadvisor.ca/Hotel_Review-g499241-d262655-Reviews-or180-Oak_Island_Resort_Conference_Centre-Western_Shore_Southwest_Nova_Scotia_N

TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
5.0
5.0
5.0
5.0
4.0
https://www.tripadvisor.ca/Hotel_Review-g499335-d262842-Reviews-or155-Auberge_West_Brome-Brome_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
5.0
4.0
3.0
5.0
4.0
https://www.tripadvisor.ca/Hotel_Review-g499335-d262842-Reviews-or160-Auberge_West_Brome-Brome_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
https://www.tripadvisor.ca/Hotel_Review-g499335-d262842-Reviews-or165-Auberge_West_Brome-Brome_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
5.0
5.0
4.0
5.0
5.0
https://www.tripadvisor.ca/Hotel_Review-g499335-d262842-Reviews-or170-Auberge_West_Brome-Brome_Quebec.html
TripAdvisor- hotel HTML page downloaded successfully..
File read successfully..
4.0
3.0
5.0
5.0
5.0
https://www.tripadvisor.ca/Hotel_Review-g499335-d262842-Reviews-or175-Auberge_West_Brome-Bro

IndexError: index 8997 is out of bounds for axis 0 with size 8996

In [17]:
# For the first batch create dataframe and write the collected information into a fresh file.
if batch != 'second':
    # Create single dataframe of collected hotel information.
    hotel_info_df = pd.DataFrame()
    hotel_info_df['id'] = hotel_id
    hotel_info_df['hotel_name'] = hotel_name
    hotel_info_df['hotel_rating'] = hotel_overall_rating
    hotel_info_df['hotel_experience'] = hotel_overall_rating_words
    hotel_info_df['amenities'] = amenities
    hotel_info_df['address'] = address
    hotel_info_df['country'] = country
    hotel_info_df['locality'] = locality_name
    hotel_info_df['location'] = lat_lon
    hotel_info_df['price'] = hotel_price

    # Write dataframe to csv and json format files.
    hotel_info_df.drop_duplicates(subset=['hotel_name'], inplace=True)
    hotel_info_df.to_json('Project-Dataset/final-data/hotel_info.json')
    hotel_info_df.to_csv('Project-Dataset/final-data/hotel_info.csv', index=False)

    print('Hotel Dataframe updated..')

In [25]:
print(len(hotel_info_df))
hotel_info_df.head(50)

3692


id                                         hotel_name hotel_rating  \
0    1       Niagara Falls Marriott Fallsview Hotel & Spa          4.0   
1    2                                Fairmont Royal York          4.5   
2    3                                 Blue Horizon Hotel          4.5   
3    4                      Fairmont Le Chateau Frontenac          4.5   
4    5                               Rimrock Resort Hotel          4.5   
5    6                Niagara Falls Marriott on the Falls          4.0   
6    7                                        The Burrard          4.0   
7    8                    One King West Hotel & Residence          4.5   
8    9                  Le Square Phillips Hotel & Suites          4.5   
9   10      Banff Park Lodge Resort and Conference Centre          4.0   
10  11                 Best Western Plus Waterfront Hotel          4.0   
11  12  Country Inn & Suites by Radisson, Niagara Fall...          4.5   
12  13                Best Western Plus Chateau Granville          4.0   
13  14                             Novotel Toronto Centre                
14  15           The Westin Trillium House, Blue Mountain          4.0   
15  16             Hotel Le Dauphin Montreal Centre-Ville          4.5   
16  17                  Chateau Victoria Hotel and Suites          4.5   
17  18                                  L'Hermitage Hotel          5.0   
18  19                                Hotel Grand Pacific          4.5   
19  20                                         Lord Elgin          4.5   
20  21                                   Le Saint-Sulpice          4.5   
21  22                             Moose Hotel and Suites          4.5   
22  23                              Pan Pacific Vancouver          4.5   
23  24          Coast Coal Harbour Vancouver Hotel by APA          4.5   
24  25                       Fairmont Chateau Lake Louise          4.5   
25  26                        Summit Lodge Boutique Hotel                
26  27                   Delta Hotels by Marriott Toronto          4.5   
27  28                      Acclaim Hotel Calgary Airport          4.5   
28  29                                    Hotel Le Priori          4.5   
29  30              Radisson Admiral Toronto Harbourfront                
30  31                                   Mount Robson Inn          4.0   
31  32                                     Crimson Jasper          4.0   
32  33                                    Bear Hill Lodge          4.0   
33  34                                     Chateau Jasper          3.5   
34  35                                      Maligne Lodge          3.5   
35  36                                       Marmot Lodge          4.0   
37  38                                        Tonquin Inn          3.5   
38  39                         Fairmont Jasper Park Lodge          4.0   
39  40          Sawridge Inn and Conference Centre Jasper          4.0   
40  41                                     Lobstick Lodge          3.0   
41  42                                Pyramid Lake Resort                
42  43                                Jasper Inn & Suites          4.0   
43  44                                    Athabasca Hotel          3.5   
44  45                                      Whistlers Inn          3.5   
45  46                                          HI Jasper          3.5   
46  47                                      Astoria Hotel          2.5   
47  48                                    Sleepy Bear Inn                
48  49                          Overlander Mountain Lodge          4.0   
49  50                     Patricia Lake Bungalows Resort          4.5   
50  51                                The White Brick Inn          5.0   

   hotel_experience                                          amenities  \
0         Very good  [Pool, Restaurant, Fitness Centre with Gym / W...   
1         Excellent  [Restaurant, Room service, Fitness Centre with...   
2      

In [32]:
# For the first batch create dataframe and write the collected information into a fresh file
if batch != 'second':
    # Create single dataframe of collected review information.
    review_df = pd.DataFrame()
    review_df['id'] = review_id
    review_df['user_rating'] = user_ratings
    review_df['user_name'] = user_name
    review_df['user_profile'] = user_profile
    review_df['user_review'] = user_review
    review_df['user_reviewdate'] = user_reviewdate
    review_df['user_staydate'] = user_staydate

    # Write dataframe to csv and json format files.
    review_df.drop_duplicates(subset=['user_name', 'id'], inplace=True)
    review_df.to_json('Project-Dataset/final-data/reviews.json')
    review_df.to_csv('Project-Dataset/final-data/reviews.csv', index=False)
    print('review DataFrame updated..')

review DataFrame updated..


In [33]:
print(len(review_df))
review_df.head(200)

175791


id user_rating                  user_name  \
0     1           5  Billy Banda Gizmo Dorothy   
1     1           4        VisitorfromOntario9   
2     1           5              Odyssey624335   
3     1           5                  Melissa F   
4     1           5          2kidswilltravel37   
5     1         nil                              
20    1           4            marysevigneault   
21    1           4              HappyToTravel   
22    1           5                    Mabdad1   
23    1           4                     Nate D   
24    1           5                 LeeLee7576   
35    1           5                   Amron304   
36    1           5                 Beatriz FV   
37    1           4                     Paul C   
38    1           4                 Michelle J   
39    1           4                lisamax0707   
45    1           5                     Kris E   
46    1           4                        R M   
47    1           5                     KIMANN   
48    1           5            Holly Theriault   
49    1           5                     wrossi   
50    1           3            loriannoliveira   
51    1           4            monolithtravels   
52    1           5                   george45   
53    1           1                     Dana N   
54    1           3            ShellsEastCoast   
60    1           5                    Frank G   
61    1           3                   ROBBO131   
62    1           3                  Sandy_B56   
63    1           5                      Jim M   
..   ..         ...                        ...   
250   2           5                    Scott R   
251   2           5           Flyer56116488775   
252   2           5                     pattdf   
253   2           4       Navigator52251511636   
254   2           5                 Michelle S   
255   2           1            Roam11136951366   
256   2           4                   Kaleem M   
257   2           5        Paradise64801670664   
258   2           3              christonsberg   
259   2           5                    Mabdad1   
265   2           5          Global24649489861   
266   2           5                      Anu C   
267   2           5                   klangdon   
268   2           4               johnmQ4443SR   
269   2           5          Roving52559252762   
280   2           4                   peiberni   
281   2           3                  sjcan8119   
282   2           5            Roam18500451867   
283   2           5                  Gloria787   
284   2           5                    DougWat   
285   2           5                    GEM1999   
286   2           5                    Kathy A   
287   2           5                   joseph h   
288   2           5           LindaKBarrie2014   
289   2           4                allanbowers   
290   2           5                 ldhead0223   
291   2           5             112RedPatchBoy   
292   2           4                 AmyLee1288   
293   2           5                        TeH   
294   2           5       Excursion63539195658   

                                          user_profile  \
0        https://www.tripadvisor.ca/Profile/Gizmo4ever   
1    https://www.tripadvisor.ca/Profile/Visitorfrom...   
2     https://www.tripadvisor.ca/Profile/Odyssey624335   
3       https://www.tripadvisor.ca/Profile/956melissaf   
4    https://www.tripadvisor.ca/Profile/2kidswilltr...   
5                                                  nil   
20   https://www.tripadvisor.ca/Profile/marysevigne...   
21      https://www.tripadvisor.ca/Profile/No_Repeat12   
22          https://www.tripadvisor.ca/Profile/Mabdad1   
23         https://www.tripadvisor.ca/Profile/nated602   
24       https://www.tripadvisor.ca/Profile/LeeLee7576   
35         https://www.tripadvisor.ca/Profile/Amron304   
36      https://www.tripadvisor.ca/Profile/beatrizfv19   
37         https://www.tripadvisor.ca/Profile/paulc726   
38     https://www.tripadvisor.ca/

In [10]:
# For second batch, create dataframe and append the information to already created files.
if batch == 'second':
     # Create single dataframe of collected hotel information.
    hotel_info_df = pd.DataFrame()
    hotel_info_df['id'] = hotel_id
    hotel_info_df['hotel_name'] = hotel_name
    hotel_info_df['hotel_rating'] = hotel_overall_rating
    hotel_info_df['hotel_experience'] = hotel_overall_rating_words
    hotel_info_df['amenities'] = amenities
    hotel_info_df['address'] = address
    hotel_info_df['country'] = country
    hotel_info_df['locality'] = locality_name
    hotel_info_df['location'] = lat_lon
    hotel_info_df['price'] = hotel_price

    # Drop duplicates by hotel name.
    hotel_info_df.drop_duplicates(subset=['hotel_name'], inplace=True)
    hotel_info_df.drop(['locality'], axis = 1, inplace=True)

    #  Append to hotel-info.csv and hotel-info.json files. 
    with open('Project-Dataset/final-data/hotel_info.json', 'a') as fd_hotel:
        hotel_info_df.to_json(fd_hotel)
    with open('Project-Dataset/final-data/hotel_info.csv', 'a') as fd1_hotel:
        hotel_info_df.to_csv(fd1_hotel, index=False, header=False)
        
    print('Hotel Dataframe updated..')

    # Create single dataframe of collected review information.
    review_df = pd.DataFrame()
    review_df['id'] = review_id
    review_df['user_rating'] = user_ratings
    review_df['user_name'] = user_name
    review_df['user_profile'] = user_profile
    review_df['user_review'] = user_review
    review_df['user_reviewdate'] = user_reviewdate
    review_df['user_staydate'] = user_staydate

    # Drop duplicate reviews by user and for a the same hotel.
    review_df.drop_duplicates(subset=['user_name', 'id'], inplace=True)
    
     #  Append to reviews.csv and reviews.json files.
    with open('Project-Dataset/final-data/reviews.json', 'a') as fd_review:
        review_df.to_json(fd_review)
    with open('Project-Dataset/final-data/reviews.csv', 'a') as fd1_review:
        review_df.to_csv(fd1_review, index=False, header=False)
        
    print('review DataFrame updated..')

Hotel Dataframe updated..
review DataFrame updated..


In [66]:
# After appending batch 2 information onto files, read them and write it back freshly.
if batch == 'second':
    hotel_full_info_df = pd.read_csv("Project-Dataset/final-data/hotel_info.csv")
    # print(len(hotel_full_urllist))
    print('Hotel urls CSV file read successfully..')

    hotel_full_info_df.drop_duplicates(subset=['hotel_name'], inplace=True)
    # hotel_full_info_df.drop(['locality'], axis = 1, inplace=True)
    print(len(hotel_full_info_df))

    #  Write to csv and json files.
    hotel_full_info_df.to_json('Project-Dataset/final-data/hotel_info.json')
    hotel_full_info_df.to_csv('Project-Dataset/final-data/hotel_info.csv', index=False)

    print('Hotel Dataframe updated..')
    hotel_full_info_df.head(5500)

Hotel urls CSV file read successfully..
5985
Hotel Dataframe updated..


id                                         hotel_name  hotel_rating  \
0        1       Niagara Falls Marriott Fallsview Hotel & Spa           4.0   
1        2                                Fairmont Royal York           4.5   
2        3                                 Blue Horizon Hotel           4.5   
3        4                      Fairmont Le Chateau Frontenac           4.5   
4        5                               Rimrock Resort Hotel           4.5   
5        6                Niagara Falls Marriott on the Falls           4.0   
6        7                                        The Burrard           4.0   
7        8                    One King West Hotel & Residence           4.5   
8        9                  Le Square Phillips Hotel & Suites           4.5   
9       10      Banff Park Lodge Resort and Conference Centre           4.0   
10      11                 Best Western Plus Waterfront Hotel           4.0   
11      12  Country Inn & Suites by Radisson, Niagara Fall...           4.5   
12      13                Best Western Plus Chateau Granville           4.0   
13      14                             Novotel Toronto Centre           NaN   
14      15           The Westin Trillium House, Blue Mountain           4.0   
15      16             Hotel Le Dauphin Montreal Centre-Ville           4.5   
16      17                  Chateau Victoria Hotel and Suites           4.5   
17      18                                  L'Hermitage Hotel           5.0   
18      19                                Hotel Grand Pacific           4.5   
19      20                                         Lord Elgin           4.5   
20      21                                   Le Saint-Sulpice           4.5   
21      22                             Moose Hotel and Suites           4.5   
22      23                              Pan Pacific Vancouver           4.5   
23      24          Coast Coal Harbour Vancouver Hotel by APA           4.5   
24      25                       Fairmont Chateau Lake Louise           4.5   
25      26                        Summit Lodge Boutique Hotel           NaN   
26      27                   Delta Hotels by Marriott Toronto           4.5   
27      28                      Acclaim Hotel Calgary Airport           4.5   
28      29                                    Hotel Le Priori           4.5   
29      30              Radisson Admiral Toronto Harbourfront           NaN   
...    ...                                                ...           ...   
5470  5575                               Cardinal Court Motel           4.0   
5471  5576                                         Glen Haven           1.0   
5472  5577                            Conny's B&B On The Farm           5.0   
5473  5578                Wedgwood Manor and Glamping Retreat           NaN   
5474  5579        Kootenay Lakeview Spa Resort & Event Centre           4.0   
5475  5580                              Little Little Retreat           NaN   
5476  5581                            Lord's Seaside Cottages           NaN   
5477  5582                                    Sal-Crest Motel           4.5   
5478  5583                  Susan's Sanctuary Bed & Breakfast           5.0   
5479  5584                         The Hive Bed and Breakfast           4.0   
5480  5585                                      Imago Village           5.0   
5481  5586                           Le Gite Du Gardien Blanc           NaN   
5482  5588                                        Maple Woods           4.5   
5483  5590                               Auberge Centre Ville           4.0   
5484  5591                                   Chateau d'Acadie           4.5   
5485  5592                                  Dunlop Lake Lodge           4.0   
5486  5593                 Holiday Inn Express Airport Dieppe           4.0   
5487  5595                             A Treasured Moment B&B           4.0   
5488  5596                                    The Grand Ho

In [11]:
# After appending batch 2 information onto files, read them and write it back freshly.
if batch == 'second':
    review_full_info_df = pd.read_csv("Project-Dataset/final-data/reviews.csv")
    # print(len(hotel_full_urllist))
    print('Review urls CSV file read successfully..')

    review_full_info_df.drop_duplicates(subset=['user_name', 'id'], inplace=True)
    review_full_info_df.dropna(inplace=True)
    print(len(review_full_info_df))

    #  Write to csv and json files.
    review_full_info_df.to_json('Project-Dataset/final-data/reviews.json')
    review_full_info_df.to_csv('Project-Dataset/final-data/reviews.csv', index=False)
        
    print('review DataFrame updated..')
    review_full_info_df.head(1000)

Review urls CSV file read successfully..
245320
review DataFrame updated..


id  user_rating                  user_name  \
0     1          5.0  Billy Banda Gizmo Dorothy   
1     1          4.0        VisitorfromOntario9   
2     1          5.0              Odyssey624335   
3     1          5.0                  Melissa F   
4     1          5.0          2kidswilltravel37   
5     1          4.0            marysevigneault   
6     1          4.0              HappyToTravel   
7     1          5.0                    Mabdad1   
8     1          4.0                     Nate D   
9     1          5.0                 LeeLee7576   
10    1          5.0                   Amron304   
11    1          5.0                 Beatriz FV   
12    1          4.0                     Paul C   
13    1          4.0                 Michelle J   
14    1          4.0                lisamax0707   
15    1          5.0                     Kris E   
16    1          4.0                        R M   
17    1          5.0                     KIMANN   
18    1          5.0            Holly Theriault   
19    1          5.0                     wrossi   
20    1          3.0            loriannoliveira   
21    1          4.0            monolithtravels   
22    1          5.0                   george45   
23    1          1.0                     Dana N   
24    1          3.0            ShellsEastCoast   
25    1          5.0                    Frank G   
26    1          3.0                   ROBBO131   
27    1          3.0                  Sandy_B56   
28    1          5.0                      Jim M   
29    1          5.0                   wftadros   
..   ..          ...                        ...   
970   7          5.0                Stephanie B   
971   7          4.0                   HTH_2212   
972   7          3.0                    Emily J   
973   7          4.0           youngtraveller61   
974   7          5.0                   lucglobe   
975   7          5.0                   sophia m   
976   8          5.0                    Karen S   
977   8          5.0                   Martin H   
978   8          5.0                   Cproskos   
979   8          5.0                      ZakHD   
980   8          5.0                      Tim M   
981   8          5.0         Cruiser56087859085   
982   8          5.0               Amanda Evans   
983   8          5.0        Discover31634018462   
984   8          5.0            Maps16425260657   
985   8          5.0                      Deb L   
986   8          5.0               kevinrE387NL   
987   8          4.0                        VJ5   
988   8          5.0                    Doris S   
989   8          5.0                   Brenda W   
990   8          5.0           Experience306542   
991   8          5.0            Maps64724666318   
992   8          5.0          Global24470514799   
993   8          5.0                    sandy p   
994   8          4.0                      Jim L   
995   8          5.0                      Eva V   
996   8          4.0                  Padraig C   
997   8          5.0                      LMnay   
998   8          5.0          Escape38199171685   
999   8          4.0                     Greg C   

                                          user_profile  \
0        https://www.tripadvisor.ca/Profile/Gizmo4ever   
1    https://www.tripadvisor.ca/Profile/Visitorfrom...   
2     https://www.tripadvisor.ca/Profile/Odyssey624335   
3       https://www.tripadvisor.ca/Profile/956melissaf   
4    https://www.tripadvisor.ca/Profile/2kidswilltr...   
5    https://www.tripadvisor.ca/Profile/marysevigne...   
6       https://www.tripadvisor.ca/Profile/No_Repeat12   
7           https://www.tripadvisor.ca/Profile/Mabdad1   
8          https://www.tripadvisor.ca/Profile/nated602   
9        https://www.tripadvisor.ca/Profile/LeeLee7576   
10         https://www.tripadvisor.ca/Profile/Amron304   
11      https://www.tripadvisor.ca/Profile/beatrizfv19   
12         https://www.tripadvisor.ca/Profile/paulc726   
13     https://www.tripadvisor